In [5]:
# !pip install emot
# !pip install symspellpy
# !pip install setuptools wheel
# !pip install spacy
# !pip install pyspellchecker
# !pip install spellchecker
# !pip install inflect
# !pip install langdetect
# !pip install google_trans_new
# !pip install deep-translator
# !pip install ekphrasis
# !pip install cdifflib
# !pip install gensim
# !pip install wordninja

  Using cached symspellpy-6.7.6-py3-none-any.whl (2.6 MB)
  Using cached editdistpy-0.1.3.tar.gz (57 kB)
  Installing build dependencies: started
  Installing build dependencies: finished with status 'done'
  Getting requirements to build wheel: started
  Getting requirements to build wheel: finished with status 'done'
    Preparing wheel metadata: started
    Preparing wheel metadata: finished with status 'done'


  ERROR: Command errored out with exit status 1:
   command: 'C:\Users\rachel\anaconda3\python.exe' 'C:\Users\rachel\anaconda3\lib\site-packages\pip\_vendor\pep517\in_process\_in_process.py' build_wheel 'C:\Users\rachel\AppData\Local\Temp\tmpjb8jambh'
       cwd: C:\Users\rachel\AppData\Local\Temp\pip-install-lwpb89oe\editdistpy_a51a9b6472f3418699a5de37094aef11
  Complete output (5 lines):
  running bdist_wheel
  running build
  running build_ext
  building 'editdistpy.levenshtein' extension
  error: Microsoft Visual C++ 14.0 or greater is required. Get it with "Microsoft C++ Build Tools": https://visualstudio.microsoft.com/visual-cpp-build-tools/
  ----------------------------------------
  ERROR: Failed building wheel for editdistpy
ERROR: Could not build wheels for editdistpy which use PEP 517 and cannot be installed directly


Failed to build editdistpy


In [1]:
import nltk
from nltk.corpus import PlaintextCorpusReader
import re, string, json

# from symspellpy.symspellpy import SymSpell, Verbosity
import pkg_resources
import spacy
from tqdm.notebook import tqdm
# from spellchecker import SpellChecker
import inflect

import difflib
import gensim

import pandas as pd

In [22]:
df = pd.read_csv("../data/usa_combined.csv")
df

Text
0       want find way end racism try force people inje...
1       this child almost died tetanus, spent months h...
2       juste se rappeler m. leblanc la pression que l...
3       you would expect cases rise significantly, cou...
4       depends whether vaccination status is embedded...
...                                                   ...
423590           do it others.... 💪🎉💉🤙 #vaccinesaveslives
423591  got my first pfizer shot today. feeling well g...
423592  #fauciouchie #2 #vaccinated #vaccinesaveslives...
423593  yay 🙌🏻 congrats dr. j being fully vaccinated i...
423594  we all have do our part end this pandemic— get...

[423595 rows x 1 columns]

In [3]:
df.drop_duplicates(keep='first', inplace=True)

In [23]:
df

Text
0       want find way end racism try force people inje...
1       this child almost died tetanus, spent months h...
2       juste se rappeler m. leblanc la pression que l...
3       you would expect cases rise significantly, cou...
4       depends whether vaccination status is embedded...
...                                                   ...
423590           do it others.... 💪🎉💉🤙 #vaccinesaveslives
423591  got my first pfizer shot today. feeling well g...
423592  #fauciouchie #2 #vaccinated #vaccinesaveslives...
423593  yay 🙌🏻 congrats dr. j being fully vaccinated i...
423594  we all have do our part end this pandemic— get...

[423595 rows x 1 columns]

## Used hashtags

In [5]:
text = df['Text']
hashtag_list = []
for tweet in text:
#     print(tweet)
    hashtags = re.findall("#[A-Za-z0-9_]+", tweet)
    if len(hashtags) > 0:
        for tag in hashtags:
            hashtag_list.append(tag)

In [6]:
hashtag_list

['#covidvaccineconfidence',
 '#vanguardvaccinationproject',
 '#populationcontrol',
 '#omicron',
 '#vaccination',
 '#mentalhealth',
 '#psychtwitter',
 '#cdnpoli',
 '#onpoli',
 '#covid19',
 '#l',
 '#polqc',
 '#getvaccinated',
 '#vaccineswork',
 '#canada',
 '#superbowlmusicfest',
 '#socal',
 '#superbowlexperience',
 '#sblvi',
 '#hiringphenomenaltalent',
 '#security',
 '#covid19vaccine',
 '#vhcon',
 '#covid19vaccine',
 '#vhcon',
 '#covid19vaccine',
 '#vhcon',
 '#legaultmustresign',
 '#legault',
 '#covid19',
 '#localnews',
 '#newsbreak',
 '#covid',
 '#defundcbc',
 '#defundbbc',
 '#nyc',
 '#godblessamerica',
 '#nonads',
 '#votehelenkicknadlerny10',
 '#dyk',
 '#fightflu',
 '#heartmonth',
 '#nowplaying',
 '#nowspinning',
 '#np',
 '#nowstreaming',
 '#subgenius',
 '#joerogan',
 '#antivaxxers',
 '#covidab',
 '#covid19',
 '#repnotrip',
 '#ableg',
 '#ciuss_mcq',
 '#covid19',
 '#ambulance',
 '#inacceptable',
 '#k',
 '#jdq',
 '#covid19',
 '#mybodymychoice',
 '#rosiebartonappreciationday',
 '#ohio',
 

## Emoji Processing

In [7]:
import pickle
from emot.emo_unicode import UNICODE_EMOJI, EMOTICONS_EMO

In [8]:
# # 'Emoji_Dict.p'- download link https://drive.google.com/open?id=1G1vIkkbqPBYPKHcQ8qy0G2zkoab2Qv4v
with open('./Emoji_Dict.p', 'rb') as fp:
    Emoji_Dict = pickle.load(fp)
Emoji_Dict = {v: k for k, v in Emoji_Dict.items()}

# # Function for converting emojis into word
def convert_emojis(text):
    for emot in UNICODE_EMOJI:
        text = text.replace(emot, "_".join(UNICODE_EMOJI[emot].replace(",","").replace(":","").split()))
    return text

In [9]:
# TEST: line of text before emoji processing
df["Text"][107]

'amoa resort has activated its covid-19 protocols will welcome guests as it strictly observes social distancing, face masks wearing enforce vaccination cards-only entry.'

In [10]:
# TEST: convert_emoji function
convert_emojis(df['Text'][107])

'amoa resort has activated its covid-19 protocols will welcome guests as it strictly observes social distancing, face masks wearing enforce vaccination cards-only entry.'

In [ ]:
# emoji processing on df["text"] column

df["Text"] = df["Text"].astype(str)
df["new_text"] = df["Text"].apply(convert_emojis)

In [ ]:
df["new_text"][107]

## Emoticon Processing

In [11]:
# 'Emoticon_Dict.p'- download link https://drive.google.com/open?id=1HDpafp97gCl9xZTQWMgP2kKK_NuhENlE
with open('./Emoticon_Dict.p', 'rb') as fp:
    Emoticon_Dict = pickle.load(fp)
    
# Function for converting emoticons into word
def convert_emoticons(text):
    for emot in EMOTICONS_EMO:
        text = text.replace(emot, "_".join(EMOTICONS_EMO[emot].replace(",","").replace(":","").split()))
    return text

In [47]:
# TEST: convert_emoticons function
sentence_listtext = "Hello :-) :-)"
convert_emoticons(sentence_listtext)

'Hello Happy_face_smiley Happy_face_smiley'

In [12]:
df["new_text"] = df["new_text"].apply(convert_emoticons)

In [13]:
df.head()

Text  \
0  want find way end racism try force people inje...   
1  this child almost died tetanus, spent months h...   
2  juste se rappeler m. leblanc la pression que l...   
3  you would expect cases rise significantly, cou...   
4  depends whether vaccination status is embedded...   

                                            new_text  
0  want find way end racism try force people inje...  
1  this child almost died tetanus, spent months h...  
2  juste se rappeler m. leblanc la pression que l...  
3  you would expect cases rise significantly, cou...  
4  depends whether vaccination status is embedded...

In [14]:
# to deal with utf-8 that pycld can't handle
import regex

RE_BAD_CHARS = regex.compile(r"\p{Cc}|\p{Cs}")

def remove_bad_chars(text):
    return RE_BAD_CHARS.sub("", text)

remove_bad_chars("A\x96 bad char")  # Cc category
# 'A bad char'

'A bad char'

In [15]:
df['new_text'] = df['new_text'].apply(remove_bad_chars)

## Detecting Languages

In [16]:
import pycld2 as cld2

tweets = df['new_text']
language = []

for each in tweets:
    text_content = each
    _, _, _, detected_language = cld2.detect(text_content, returnVectors=True)
    language.append(detected_language)

In [17]:
langs = []

for each in language:
    lang_detected = ""
    for i in range(0,len(each)):
        lang_extracted = each[i][2]
        if i != (len(each) - 1):
            lang_detected += lang_extracted + ", "
        else:
            lang_detected += lang_extracted
    langs.append(lang_detected)

In [18]:
langs

['ENGLISH',
 'ENGLISH',
 'FRENCH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'Unknown',
 'ENGLISH',
 'FRENCH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'FRENCH',
 'ENGLISH',
 'ENGLISH',
 'FRENCH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'FRENCH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'FRENCH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'Unknown',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'Unknown',
 'FRENCH',
 'ENGLISH',
 'FRENCH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',


In [19]:
df['languages'] = langs
df

Text  \
0       want find way end racism try force people inje...   
1       this child almost died tetanus, spent months h...   
2       juste se rappeler m. leblanc la pression que l...   
3       you would expect cases rise significantly, cou...   
4       depends whether vaccination status is embedded...   
...                                                   ...   
423588  if you are eligible, please pre- register covi...   
423590           do it others.... 💪🎉💉🤙 #vaccinesaveslives   
423592  #fauciouchie #2 #vaccinated #vaccinesaveslives...   
423593  yay 🙌🏻 congrats dr. j being fully vaccinated i...   
423594  we all have do our part end this pandemic— get...   

                                                 new_text languages  
0       want find way end racism try force people inje...   ENGLISH  
1       this child almost died tetanus, spent months h...   ENGLISH  
2       juste se rappeler m. leblanc la pression que l...    FRENCH  
3       you would expect cases rise significantly, cou...   ENGLISH  
4       depends whether vaccination status is embedded...   ENGLISH  
...                                                   ...       ...  
423588  if you are eligible, please pre- register covi...   ENGLISH  
423590  do it others.... flexed_bicepsparty_poppersyri...   ENGLISH  
423592  #fauciouchie #2 #vaccinated #vaccinesaveslives...   Unknown  
423593  yay raising_handslight_skin_tone congrats dr. ...   ENGLISH  
423594  we all have do our part end this pandemic— get...   ENGLISH  

[404337 rows x 3 columns]

In [20]:
df[df['languages'] != 'ENGLISH'].head()
#check how many rows

Text  \
2   juste se rappeler m. leblanc la pression que l...   
13                                        vaccination   
15  1-je comprends exactement ce qui doit être com...   
35  environ 500 médecins spécialistes participaien...   
38  c'est bien dommage que ce soit un droit, leur ...   

                                             new_text languages  
2   juste se rappeler m. leblanc la pression que l...    FRENCH  
13                                        vaccination   Unknown  
15  1-je comprends exactement ce qui doit être com...    FRENCH  
35  environ 500 médecins spécialistes participaien...    FRENCH  
38  c'est bien dommage que ce soit un droit, leur ...    FRENCH

In [21]:
df[df['languages'] != 'ENGLISH']['new_text']

2         juste se rappeler m. leblanc la pression que l...
13                                              vaccination
15        1-je comprends exactement ce qui doit être com...
35        environ 500 médecins spécialistes participaien...
38        c'est bien dommage que ce soit un droit, leur ...
                                ...                        
423579                             ayep. #vaccinesaveslives
423582    continue wear your mask preferably double , ge...
423585        #vaccinated #vaccinesaveslives syringemicrobe
423586    #vaccine #maskup #vaccinesaveslives #vaccinesi...
423592    #fauciouchie #2 #vaccinated #vaccinesaveslives...
Name: new_text, Length: 56002, dtype: object

In [91]:
df[df['languages'] != 'ENGLISH']['new_text'][105977]

'it’s time you do your part this fight against covid we reward you your actions we are sure we together be victorious this fight with collective effort everyone raising_handsmedium_skin_tone #vaccinesaveslives #weareinthistogether #plasmadonation #spreadpositivity'

In [22]:
df.to_csv('usa_after_language_detection.csv')

## Language Translation

In [1]:
# df = pd.read_csv('../data/usa_after_language_detection.csv')

In [ ]:
from deep_translator import GoogleTranslator

non_english = df[df['languages'] != 'ENGLISH']['new_text']

translated = []

for each in non_english:
    translate = GoogleTranslator(source='auto', target='en').translate(each)
    translated.append(translate)

In [ ]:
translated

In [ ]:
#creating new_text column
df['new_text'] = df['Text']

In [ ]:
non_english = df[df['languages'] != 'ENGLISH']

In [ ]:
non_english.head()
#33981 rows

In [ ]:
indexes_list = non_english.index

In [ ]:
indexes_list

In [ ]:
len(indexes_list)

In [ ]:
# range_firstNum = start_range + start_batch

# new_indexes_list = []

# for num in indexes_list:
#     new = num - range_firstNum
#     new_indexes_list.append(new)

In [ ]:
for i in range(0,len(indexes_list)):
    index = indexes_list[i]
    df.iloc[index]['new_text'] = translated[i]

In [ ]:
#check that the new_text col to see to check that the initial non-english rows have been translated
df[df['languages'] != 'ENGLISH']

## Language Detection Part 2

In [ ]:
# import pycld2 as cld2

# reviews = df['new_text_after_translation']
# language2 = []

# for each in reviews:
#     text_content = each
#     _, _, _, detected_language = cld2.detect(text_content, returnVectors=True)
#     language2.append(detected_language)

In [ ]:
# langs2 = []

# for each in language2:
#     lang_detected = ""
#     for i in range(0,len(each)):
#         lang_extracted = each[i][2]
#         if i != (len(each) - 1):
#             lang_detected += lang_extracted + ", "
#         else:
#             lang_detected += lang_extracted
#     langs2.append(lang_detected)

In [ ]:
# langs2

In [ ]:
# df['new_languages'] = langs2

In [ ]:
# df.to_csv("usa-after-langdetectandtrans.csv")

In [ ]:
# non_english2 = df[df['new_languages'] != 'ENGLISH']
# non_english2

In [ ]:
#see how many still detected as non-english, brieflcheck is it rly non english
# non_english2.info()

In [ ]:
# non_english2.to_csv('non_english2.csv')

## Read df after translation (USA)

In [63]:
df = pd.read_csv('./df_after_translation_usa.csv')

In [64]:
df.head()

Unnamed: 0                                               Text  \
0           0  want find way end racism try force people inje...   
1           1  this child almost died tetanus, spent months h...   
2           2  juste se rappeler m. leblanc la pression que l...   
3           3  you would expect cases rise significantly, cou...   
4           4  depends whether vaccination status is embedded...   

                                            new_text languages  \
0  want find way end racism try force people inje...   ENGLISH   
1  this child almost died tetanus, spent months h...   ENGLISH   
2  juste se rappeler m. leblanc la pression que l...    FRENCH   
3  you would expect cases rise significantly, cou...   ENGLISH   
4  depends whether vaccination status is embedded...   ENGLISH   

                          new_text_after_translation  
0  want find way end racism try force people inje...  
1  this child almost died tetanus, spent months h...  
2  just remember mr. leblanc the pressure that th...  
3  you would expect cases rise significantly, cou...  
4  depends whether vaccination status is embedded...

In [65]:
df

Unnamed: 0                                               Text  \
0                0  want find way end racism try force people inje...   
1                1  this child almost died tetanus, spent months h...   
2                2  juste se rappeler m. leblanc la pression que l...   
3                3  you would expect cases rise significantly, cou...   
4                4  depends whether vaccination status is embedded...   
...            ...                                                ...   
404260      404260  if you are eligible, please pre- register covi...   
404261      404261           do it others.... 💪🎉💉🤙 #vaccinesaveslives   
404262      404262  #fauciouchie #2 #vaccinated #vaccinesaveslives...   
404263      404263  yay 🙌🏻 congrats dr. j being fully vaccinated i...   
404264      404264  we all have do our part end this pandemic— get...   

                                                 new_text languages  \
0       want find way end racism try force people inje...   ENGLISH   
1       this child almost died tetanus, spent months h...   ENGLISH   
2       juste se rappeler m. leblanc la pression que l...    FRENCH   
3       you would expect cases rise significantly, cou...   ENGLISH   
4       depends whether vaccination status is embedded...   ENGLISH   
...                                                   ...       ...   
404260  if you are eligible, please pre- register covi...   ENGLISH   
404261  do it others.... flexed_bicepsparty_poppersyri...   ENGLISH   
404262  #fauciouchie #2 #vaccinated #vaccinesaveslives...   ENGLISH   
404263  yay raising_handslight_skin_tone congrats dr. ...   ENGLISH   
404264  we all have do our part end this pandemic— get...   ENGLISH   

                               new_text_after_translation  
0       want find way end racism try force people inje...  
1       this child almost died tetanus, spent months h...  
2       just remember mr. leblanc the pressure that th...  
3       you would expect cases rise significantly, cou...  
4       depends whether vaccination status is embedded...  
...                                                   ...  
404260  if you are eligible, please pre- register covi...  
404261  do it others.... flexed_bicepsparty_poppersyri...  
404262  #fauciouchie #2 #vaccinated #vaccinesaveslives...  
404263  yay raising_handslight_skin_tone congrats dr. ...  
404264  we all have do our part end this pandemic— get...  

[404265 rows x 5 columns]

In [66]:
df.drop('Unnamed: 0', axis=1, inplace=True)

In [67]:
df

Text  \
0       want find way end racism try force people inje...   
1       this child almost died tetanus, spent months h...   
2       juste se rappeler m. leblanc la pression que l...   
3       you would expect cases rise significantly, cou...   
4       depends whether vaccination status is embedded...   
...                                                   ...   
404260  if you are eligible, please pre- register covi...   
404261           do it others.... 💪🎉💉🤙 #vaccinesaveslives   
404262  #fauciouchie #2 #vaccinated #vaccinesaveslives...   
404263  yay 🙌🏻 congrats dr. j being fully vaccinated i...   
404264  we all have do our part end this pandemic— get...   

                                                 new_text languages  \
0       want find way end racism try force people inje...   ENGLISH   
1       this child almost died tetanus, spent months h...   ENGLISH   
2       juste se rappeler m. leblanc la pression que l...    FRENCH   
3       you would expect cases rise significantly, cou...   ENGLISH   
4       depends whether vaccination status is embedded...   ENGLISH   
...                                                   ...       ...   
404260  if you are eligible, please pre- register covi...   ENGLISH   
404261  do it others.... flexed_bicepsparty_poppersyri...   ENGLISH   
404262  #fauciouchie #2 #vaccinated #vaccinesaveslives...   ENGLISH   
404263  yay raising_handslight_skin_tone congrats dr. ...   ENGLISH   
404264  we all have do our part end this pandemic— get...   ENGLISH   

                               new_text_after_translation  
0       want find way end racism try force people inje...  
1       this child almost died tetanus, spent months h...  
2       just remember mr. leblanc the pressure that th...  
3       you would expect cases rise significantly, cou...  
4       depends whether vaccination status is embedded...  
...                                                   ...  
404260  if you are eligible, please pre- register covi...  
404261  do it others.... flexed_bicepsparty_poppersyri...  
404262  #fauciouchie #2 #vaccinated #vaccinesaveslives...  
404263  yay raising_handslight_skin_tone congrats dr. ...  
404264  we all have do our part end this pandemic— get...  

[404265 rows x 4 columns]

## Text File & Corpus Creation

In [8]:
# create txt file for each text review

# def CreateCorpusFromDataFrame(corpusfolder, df):
#     for index, r in df.iterrows():
#     # print (r['text'])
#     # print (str(index) + '.txt')
#         text = r['new_text_after_translation']
#         fname = str(index)+'.txt'
#         corpusfile = open(corpusfolder+'/'+fname, "w", encoding="utf-8")
#         corpusfile.write(str(text))
#         corpusfile.close()

# CreateCorpusFromDataFrame('../text-corpus-usa-v2', df)

# reference: https://stackoverflow.com/questions/49088978/how-to-create-corpus-from-pandas-data-frame-to-operate-with-nltk/49104725

In [2]:
file_directory = '../text-corpus-usa-v2'
filename_pattern = '.+\.txt'

my_corpus = PlaintextCorpusReader(file_directory, filename_pattern)

#Print some words in specific file
test = my_corpus.words('0.txt')
print(test)
print(len(test))

['want', 'find', 'way', 'end', 'racism', 'try', ...]
52


In [3]:
#Total number of text files i.e. total number of tweets
print(len(my_corpus.fileids()))

404265


In [12]:
fdist = nltk.FreqDist(test)
print(fdist.most_common(10))

[('people', 4), ('.', 4), ('i', 3), ('force', 2), ('against', 2), ('vaxx', 2), ('want', 1), ('find', 1), ('way', 1), ('end', 1)]


In [ ]:
# word distribution across all files
fdist_all_files = nltk.FreqDist(my_corpus.words())
print(fdist_all_files.most_common(10))

In [ ]:
#total number of words
total_words = my_corpus.words()
print(total_words)
print(len(total_words))

## Tokenization

In [24]:
#Creating a sorted list of texts since my_corpus.fileids() does not read texts consecutively
#EDIT RANGE
sorted_list = [f'{i}.txt' for i in range(18000, 19000)]

In [25]:
tokenised_words = [my_corpus.words(each) for each in sorted_list]
tokenised_words

[['i', "'", 'd', 'say', 'that', 'even', 'more', '.', ...],
 ['happy', 'as', 'hell', 'i', 'figured', 'out', 'how', ...],
 ['by', 'post', 'pandemic', 'they', 'mean', ...],
 ['i', '’', 'm', 'not', 'gonna', 'watch', 'guy', 'who', ...],
 ['measles', 'outbreak', 'afghanistan', 'has', 'killed', ...],
 ['immune', 'response', 'prior', 'infection', 'was', ...],
 ['"', 'proposed', 'georgia', 'law', 'get', 'rid', ...],
 ['bro', 'who', 'asked', 'loudly_crying_face', 'not', ...],
 ['except', 'all', 'diseases', 'that', 'have', 'been', ...],
 ['as', 'reminder', 'today', "'", 's', '2', '/', '6', ...],
 ['deadlines', 'healthcare', 'workers', 'be', 'fully', ...],
 ['alternatively', ',', 'allow', 'cbsa', 'employee', ...],
 ['it', '’', 's', 'really', 'not', 'presidents', ...],
 ['nice', '.', 'i', 'think', 'our', 'culture', 'has', ...],
 ['police_car_lightit', '’', 's', 'game', 'day', ...],
 ['how', 'did', 'that', 'mass', 'vaccination', ...],
 ['consequences', '.', 'right', 'start', ',', 'experts', ...],
 [

In [26]:
print(len(tokenised_words))

1000


## Converting British to American English

In [27]:
#https://stackoverflow.com/questions/42329766/python-nlp-british-english-vs-american-english

import requests

def americanize(word):
    url ="https://raw.githubusercontent.com/hyperreality/American-British-English-Translator/master/data/british_spellings.json"
    british_to_american_dict = requests.get(url).json()

    for british_spelling, american_spelling in british_to_american_dict.items():
        word = word.replace(british_spelling, american_spelling)
  
    return word

In [28]:
test_americanize = [['flavour', 'colour'], ['apologise', 'travelled']]
test_americanize = [[americanize(w) for w in each] for each in test_americanize]
test_americanize

[['flavor', 'color'], ['apologize', 'traveled']]

In [29]:
tokenised = [[americanize(w) for w in each] for each in tokenised_words]
tokenised

[['i',
  "'",
  'd',
  'say',
  'that',
  'even',
  'more',
  '.',
  'fully',
  'vaccination',
  'doesn',
  "'",
  't',
  'prevent',
  'infection',
  'as',
  'efficiently',
  'as',
  'wearing',
  'n95',
  ';',
  'latter',
  ',',
  'regardless',
  'variant',
  '.'],
 ['happy',
  'as',
  'hell',
  'i',
  'figured',
  'out',
  'how',
  'add',
  'my',
  'vaccination',
  'my',
  'apple',
  'wallet',
  'i',
  'was',
  'tired',
  'losing',
  'damn',
  'card'],
 ['by', 'post', 'pandemic', 'they', 'mean', 'vaccination', 'i', 'presume'],
 ['i',
  '’',
  'm',
  'not',
  'gonna',
  'watch',
  'guy',
  'who',
  'made',
  'fun',
  'someone',
  '’',
  's',
  'alcoholism',
  ',',
  'cooper',
  '.',
  'or',
  'someone',
  'who',
  'bodyshamed',
  'nia',
  'jax',
  ',',
  'regardless',
  'what',
  'she',
  'said',
  'about',
  'vaccination',
  'cards',
  ',',
  'which',
  'is',
  'stupid',
  'as',
  'fuck',
  '.'],
 ['measles',
  'outbreak',
  'afghanistan',
  'has',
  'killed',
  '74',
  'kids',
  'so'

In [30]:
# save americanized tokens
convert_to_str = []

for each in tokenised:
    converted_str = ""
    for i in range(0,len(each)):
        if i == (len(each) - 1):
            converted_str += each[i]
        else:
            converted_str += each[i] + ", "
    convert_to_str.append(converted_str)
    
converted_df = pd.DataFrame(convert_to_str)

converted_df.to_csv('usa_americanized_tokens_18000-19000.csv')

## Conversion to numerals

In [31]:
#check if text has numbers 
def hasNumbers(inputList):
    for list in inputList:
        for word in list:
            if word.isdigit():
                return True
    return False

hasNumbers(tokenised)

True

In [32]:
# since theres numbers, the numbers need to be converted to words e.g. "2" to "two"

p = inflect.engine()
  
# convert number into words
def convert_number(text):
    # split string into list of words
    temp_str = text.split()
    # initialise empty list
    new_string = []
  
    for word in temp_str:
        # if word is a digit, convert the digit
        # to numbers and append into the new_string list
        if word.isdigit():
            temp = p.number_to_words(word)
            new_string.append(temp)
  
        # append the word as it is
        else:
            new_string.append(word)
  
    # join the words of new_string to form a string
    temp_str = ' '.join(new_string)
    return temp_str

In [33]:
# example text which contain numbers in it
input_list = ['There are 3 balls in this bag, and 12 in the other one.', '29']
result = [convert_number(each)for each in input_list]
result

['There are three balls in this bag, and twelve in the other one.',
 'twenty-nine']

In [34]:
#NEED TO CHANGE VARIABLE after us to brit eng conversion

tokenised_numerals_converted = [[convert_number(w) for w in each] for each in tokenised]

In [35]:
#check if text has numbers 
def hasNumbers(inputList):
    for list in inputList:
        for word in list:
            if word.isdigit():
                return True
    return False

hasNumbers(tokenised_numerals_converted)

False

## Misspellings

In [36]:
def correct_typo(tokens):
    spell = SpellChecker()
    return [spell.correction(t) if len(spell.unknown([t]))>0 else t for t in tokens]

In [37]:
misspelled_test = ['greot', 'coyor', 'and', 'misspeling']
correct_typo(misspelled_test)

['great', 'color', 'and', 'misspelling']

In [38]:
tokenised_spellchecked = [correct_typo(each) for each in tokenised_numerals_converted]

In [39]:
tokenised_spellchecked

[['i',
  "'",
  'i',
  'say',
  'that',
  'even',
  'more',
  '.',
  'fully',
  'vaccination',
  'doesn',
  "'",
  'i',
  'prevent',
  'infection',
  'as',
  'efficiently',
  'as',
  'wearing',
  'not',
  ';',
  'latter',
  ',',
  'regardless',
  'variant',
  '.'],
 ['happy',
  'as',
  'hell',
  'i',
  'figured',
  'out',
  'how',
  'add',
  'my',
  'vaccination',
  'my',
  'apple',
  'wallet',
  'i',
  'was',
  'tired',
  'losing',
  'damn',
  'card'],
 ['by', 'post', 'pandemic', 'they', 'mean', 'vaccination', 'i', 'presume'],
 ['i',
  'i',
  'i',
  'not',
  'gonna',
  'watch',
  'guy',
  'who',
  'made',
  'fun',
  'someone',
  'i',
  'i',
  'alcoholism',
  ',',
  'cooper',
  '.',
  'or',
  'someone',
  'who',
  'bodyshamed',
  'nia',
  'jax',
  ',',
  'regardless',
  'what',
  'she',
  'said',
  'about',
  'vaccination',
  'cards',
  ',',
  'which',
  'is',
  'stupid',
  'as',
  'fuck',
  '.'],
 ['measles',
  'outbreak',
  'afghanistan',
  'has',
  'killed',
  'seventy-four',
  'kid

In [40]:
convert_to_str = []

for each in tokenised_spellchecked:
    converted_str = ""
    for i in range(0,len(each)):
        if i == (len(each) - 1):
            converted_str += each[i]
        else:
            converted_str += each[i] + ", "
    convert_to_str.append(converted_str)
    
converted_df = pd.DataFrame(convert_to_str)

converted_df.to_csv('corrected-18000-19000.csv')

In [41]:
converted_df

0
0    i, ', i, say, that, even, more, ., fully, vacc...
1    happy, as, hell, i, figured, out, how, add, my...
2    by, post, pandemic, they, mean, vaccination, i...
3    i, i, i, not, gonna, watch, guy, who, made, fu...
4    measles, outbreak, afghanistan, has, killed, s...
..                                                 ...
995  i, don, i, i, know, or, care, who, needs, hear...
996  we, could, mandate, vaccination, i, -, twelve,...
997  i, know, alabama, ', i, vaccination, numbers, ...
998  you, lack, comprehension, skills, :, i, nevert...
999  cross, border, usa, or, back, requires, vaccin...

[1000 rows x 1 columns]

## Compiled CSV

In [2]:
import pandas as pd
df2 = pd.read_csv("./rachel-usa/rachel-usa-compiled.csv")

In [3]:
new_tokenised_spellchecked = []

for row in df2['0']:
    alist = row.split(", ")
    new_tokenised_spellchecked.append(alist)

In [4]:
new_tokenised_spellchecked

[['what', 'if', 'kyrie', 'gets', 'vaccinated', 'after', 'trade', 'i', 'lol'],
 ['california',
  'health',
  'officials',
  'announced',
  'monday',
  'that',
  'state',
  'i',
  'i',
  'indoor',
  'mask',
  'mandate',
  'vaccinated',
  'people',
  'is',
  'ending',
  'next',
  'week',
  '.',
  'here',
  'i',
  'i',
  'what',
  'expect',
  '.'],
 ['yes',
  ',',
  'quincy',
  'sam',
  'would',
  'figure',
  'it',
  'all',
  'out',
  'certain',
  '.',
  'good',
  'call',
  '.',
  'i',
  'will',
  'say',
  'though',
  ',',
  'we',
  'don',
  'i',
  'i',
  'want',
  'get',
  'kojak',
  'involved',
  'at',
  'all',
  '.',
  'or',
  'more',
  'recently',
  'monk',
  'would',
  'sort',
  'it',
  'all',
  'out',
  'as',
  'well',
  '.'],
 ['lol', 'it', 'was', 'not', 'just', 'getting', 'vaccinated'],
 ['ninety',
  '%',
  'truckers',
  'are',
  'double',
  'vaccinated',
  'but',
  'sure',
  'keep',
  'believing',
  'this',
  'is',
  'working',
  'class',
  'movement',
  'clown_face',
  'pile_of_p

## Convert to lowercase

In [5]:
#NEED TO CHANGE VARIABLE AFTER SPELLCHECK

tokenised_lower = [[w.lower() for w in each] for each in new_tokenised_spellchecked]
tokenised_lower

[['what', 'if', 'kyrie', 'gets', 'vaccinated', 'after', 'trade', 'i', 'lol'],
 ['california',
  'health',
  'officials',
  'announced',
  'monday',
  'that',
  'state',
  'i',
  'i',
  'indoor',
  'mask',
  'mandate',
  'vaccinated',
  'people',
  'is',
  'ending',
  'next',
  'week',
  '.',
  'here',
  'i',
  'i',
  'what',
  'expect',
  '.'],
 ['yes',
  ',',
  'quincy',
  'sam',
  'would',
  'figure',
  'it',
  'all',
  'out',
  'certain',
  '.',
  'good',
  'call',
  '.',
  'i',
  'will',
  'say',
  'though',
  ',',
  'we',
  'don',
  'i',
  'i',
  'want',
  'get',
  'kojak',
  'involved',
  'at',
  'all',
  '.',
  'or',
  'more',
  'recently',
  'monk',
  'would',
  'sort',
  'it',
  'all',
  'out',
  'as',
  'well',
  '.'],
 ['lol', 'it', 'was', 'not', 'just', 'getting', 'vaccinated'],
 ['ninety',
  '%',
  'truckers',
  'are',
  'double',
  'vaccinated',
  'but',
  'sure',
  'keep',
  'believing',
  'this',
  'is',
  'working',
  'class',
  'movement',
  'clown_face',
  'pile_of_p

## Remove punctuation

In [6]:
# remove punctuations from tokenised_lower
tokenised_words_only = [[w for w in each if re.search('^[a-z]+$',w)] for each in tokenised_lower]
tokenised_words_only

[['what', 'if', 'kyrie', 'gets', 'vaccinated', 'after', 'trade', 'i', 'lol'],
 ['california',
  'health',
  'officials',
  'announced',
  'monday',
  'that',
  'state',
  'i',
  'i',
  'indoor',
  'mask',
  'mandate',
  'vaccinated',
  'people',
  'is',
  'ending',
  'next',
  'week',
  'here',
  'i',
  'i',
  'what',
  'expect'],
 ['yes',
  'quincy',
  'sam',
  'would',
  'figure',
  'it',
  'all',
  'out',
  'certain',
  'good',
  'call',
  'i',
  'will',
  'say',
  'though',
  'we',
  'don',
  'i',
  'i',
  'want',
  'get',
  'kojak',
  'involved',
  'at',
  'all',
  'or',
  'more',
  'recently',
  'monk',
  'would',
  'sort',
  'it',
  'all',
  'out',
  'as',
  'well'],
 ['lol', 'it', 'was', 'not', 'just', 'getting', 'vaccinated'],
 ['ninety',
  'truckers',
  'are',
  'double',
  'vaccinated',
  'but',
  'sure',
  'keep',
  'believing',
  'this',
  'is',
  'working',
  'class',
  'movement'],
 ['you',
  're',
  'not',
  'talking',
  'about',
  'oxford',
  'critical',
  'theory',
  

## Remove words len <= 3

In [7]:
# new_list = []

# for alist in tokenised_words_only:
#     mini_list = []
#     for word in alist:
#         if len(word) > 3:
#             mini_list.append(word)
#     new_list.append(mini_list)

In [8]:
#test
# new_list

In [9]:
tokenised_words_only = new_list

NameError: name 'new_list' is not defined

In [10]:
tokenised_words_only

[['what', 'if', 'kyrie', 'gets', 'vaccinated', 'after', 'trade', 'i', 'lol'],
 ['california',
  'health',
  'officials',
  'announced',
  'monday',
  'that',
  'state',
  'i',
  'i',
  'indoor',
  'mask',
  'mandate',
  'vaccinated',
  'people',
  'is',
  'ending',
  'next',
  'week',
  'here',
  'i',
  'i',
  'what',
  'expect'],
 ['yes',
  'quincy',
  'sam',
  'would',
  'figure',
  'it',
  'all',
  'out',
  'certain',
  'good',
  'call',
  'i',
  'will',
  'say',
  'though',
  'we',
  'don',
  'i',
  'i',
  'want',
  'get',
  'kojak',
  'involved',
  'at',
  'all',
  'or',
  'more',
  'recently',
  'monk',
  'would',
  'sort',
  'it',
  'all',
  'out',
  'as',
  'well'],
 ['lol', 'it', 'was', 'not', 'just', 'getting', 'vaccinated'],
 ['ninety',
  'truckers',
  'are',
  'double',
  'vaccinated',
  'but',
  'sure',
  'keep',
  'believing',
  'this',
  'is',
  'working',
  'class',
  'movement'],
 ['you',
  're',
  'not',
  'talking',
  'about',
  'oxford',
  'critical',
  'theory',
  

## POS Tagging

In [11]:
tokens = tokenised_words_only[0]
tokens

['what', 'if', 'kyrie', 'gets', 'vaccinated', 'after', 'trade', 'i', 'lol']

In [12]:
# import nltk
# nltk.download('averaged_perceptron_tagger')

In [13]:
nltk.pos_tag(tokens)

[('what', 'WP'),
 ('if', 'IN'),
 ('kyrie', 'VBN'),
 ('gets', 'VBZ'),
 ('vaccinated', 'VBN'),
 ('after', 'IN'),
 ('trade', 'NN'),
 ('i', 'NN'),
 ('lol', 'VBP')]

In [14]:
pos_tagged = []

for each in tokenised_words_only:
    pos_tags = nltk.pos_tag(each)
    pos_tagged.append(pos_tags)

In [15]:
pos_tagged

[[('what', 'WP'),
  ('if', 'IN'),
  ('kyrie', 'VBN'),
  ('gets', 'VBZ'),
  ('vaccinated', 'VBN'),
  ('after', 'IN'),
  ('trade', 'NN'),
  ('i', 'NN'),
  ('lol', 'VBP')],
 [('california', 'NN'),
  ('health', 'NN'),
  ('officials', 'NNS'),
  ('announced', 'VBD'),
  ('monday', 'NN'),
  ('that', 'IN'),
  ('state', 'NN'),
  ('i', 'NN'),
  ('i', 'VBP'),
  ('indoor', 'VBP'),
  ('mask', 'JJ'),
  ('mandate', 'NN'),
  ('vaccinated', 'VBN'),
  ('people', 'NNS'),
  ('is', 'VBZ'),
  ('ending', 'VBG'),
  ('next', 'JJ'),
  ('week', 'NN'),
  ('here', 'RB'),
  ('i', 'VBZ'),
  ('i', 'VBP'),
  ('what', 'WP'),
  ('expect', 'VBP')],
 [('yes', 'RB'),
  ('quincy', 'NN'),
  ('sam', 'NN'),
  ('would', 'MD'),
  ('figure', 'VB'),
  ('it', 'PRP'),
  ('all', 'DT'),
  ('out', 'RP'),
  ('certain', 'JJ'),
  ('good', 'JJ'),
  ('call', 'NN'),
  ('i', 'NN'),
  ('will', 'MD'),
  ('say', 'VB'),
  ('though', 'IN'),
  ('we', 'PRP'),
  ('don', 'VBP'),
  ('i', 'JJ'),
  ('i', 'VBP'),
  ('want', 'VBP'),
  ('get', 'NN'),
  ('koj

In [16]:
import pandas as pd

df = pd.read_csv("./df_after_translation_usa.csv")

In [17]:
df = df.iloc[322000:]

In [18]:
df['pos_tagged_words'] = pos_tagged

In [19]:
df.head()

Unnamed: 0                                               Text  \
322000      322000      what if kyrie gets vaccinated after trade…lol   
322001      322001  california health officials announced monday t...   
322002      322002  yes, quincy sam would figure it all out certai...   
322003      322003             lol it was not just getting vaccinated   
322004      322004  90%truckers are double vaccinated but sure kee...   

                                                 new_text languages  \
322000      what if kyrie gets vaccinated after trade…lol   ENGLISH   
322001  california health officials announced monday t...   ENGLISH   
322002  yes, quincy sam would figure it all out certai...   ENGLISH   
322003             lol it was not just getting vaccinated   ENGLISH   
322004  90%truckers are double vaccinated but sure kee...   ENGLISH   

                               new_text_after_translation  \
322000      what if kyrie gets vaccinated after trade…lol   
322001  california health officials announced monday t...   
322002  yes, quincy sam would figure it all out certai...   
322003             lol it was not just getting vaccinated   
322004  90%truckers are double vaccinated but sure kee...   

                                         pos_tagged_words  
322000  [(what, WP), (if, IN), (kyrie, VBN), (gets, VB...  
322001  [(california, NN), (health, NN), (officials, N...  
322002  [(yes, RB), (quincy, NN), (sam, NN), (would, M...  
322003  [(lol, NN), (it, PRP), (was, VBD), (not, RB), ...  
322004  [(ninety, NN), (truckers, NNS), (are, VBP), (d...

## Stop word removal

In [20]:
# import nltk
# nltk.download('stopwords')

In [21]:
# TEST: remove stop words from test_words_only
from nltk.corpus import stopwords
stop_list = stopwords.words('english')

test_words_only1 = ['not', 'great', 'color', 'and', 'cruelty', 'free', 'i', 'use', 'elf', 'cosmetics', 'every', 'day', 'and', 'i', 'love', 'it']
test_stopremoved = [w for w in test_words_only1 if w not in stop_list or w == 'not']
print(test_stopremoved)

['not', 'great', 'color', 'cruelty', 'free', 'use', 'elf', 'cosmetics', 'every', 'day', 'love']


In [22]:
# remove stop words from tokenised_words_only
from nltk.corpus import stopwords
stop_list = stopwords.words('english')
tokenised_stopremoved = [[w for w in each if w not in stop_list or w == 'not'] for each in tokenised_words_only]
tokenised_stopremoved

[['kyrie', 'gets', 'vaccinated', 'trade', 'lol'],
 ['california',
  'health',
  'officials',
  'announced',
  'monday',
  'state',
  'indoor',
  'mask',
  'mandate',
  'vaccinated',
  'people',
  'ending',
  'next',
  'week',
  'expect'],
 ['yes',
  'quincy',
  'sam',
  'would',
  'figure',
  'certain',
  'good',
  'call',
  'say',
  'though',
  'want',
  'get',
  'kojak',
  'involved',
  'recently',
  'monk',
  'would',
  'sort',
  'well'],
 ['lol', 'not', 'getting', 'vaccinated'],
 ['ninety',
  'truckers',
  'double',
  'vaccinated',
  'sure',
  'keep',
  'believing',
  'working',
  'class',
  'movement'],
 ['not', 'talking', 'oxford', 'critical', 'theory', 'definition'],
 ['people',
  'milan',
  'refuse',
  'show',
  'health',
  'passport',
  'enter',
  'bars',
  'restaurants',
  'decided',
  'bring',
  'food',
  'drink',
  'home',
  'outdoor',
  'aperitif',
  'together',
  'vaccinated',
  'not',
  'happening',
  'many',
  'italian',
  'cities'],
 ['miss', 'guys'],
 ['great', 'idea'

## Bigram & Trigram Models

In [23]:
# Build the bigram and trigram models
bigram = gensim.models.Phrases(tokenised_stopremoved, min_count=5, threshold=100) # higher threshold fewer phrases.
trigram = gensim.models.Phrases(bigram[tokenised_stopremoved], threshold=100)
# Faster way to get a sentence clubbed as a trigram/bigram
bigram_mod = gensim.models.phrases.Phraser(bigram)
trigram_mod = gensim.models.phrases.Phraser(trigram)

In [24]:
def make_bigrams(texts):
    return [bigram_mod[doc] for doc in texts]
def make_trigrams(texts):
    return [trigram_mod[bigram_mod[doc]] for doc in texts]

In [25]:
# Form Bigrams
tokenised_bigrams = make_bigrams(tokenised_stopremoved)
# Form Trigrams
tokenised_trigrams = make_trigrams(tokenised_stopremoved)

In [26]:
tokenised_bigrams

[['kyrie', 'gets', 'vaccinated', 'trade', 'lol'],
 ['california',
  'health',
  'officials_announced',
  'monday',
  'state',
  'indoor',
  'mask',
  'mandate',
  'vaccinated',
  'people',
  'ending',
  'next_week',
  'expect'],
 ['yes',
  'quincy',
  'sam',
  'would',
  'figure',
  'certain',
  'good',
  'call',
  'say',
  'though',
  'want',
  'get',
  'kojak',
  'involved',
  'recently',
  'monk',
  'would',
  'sort',
  'well'],
 ['lol', 'not', 'getting', 'vaccinated'],
 ['ninety',
  'truckers',
  'double',
  'vaccinated',
  'sure',
  'keep',
  'believing',
  'working',
  'class',
  'movement'],
 ['not', 'talking', 'oxford', 'critical', 'theory', 'definition'],
 ['people',
  'milan',
  'refuse',
  'show',
  'health',
  'passport',
  'enter',
  'bars_restaurants',
  'decided',
  'bring',
  'food',
  'drink',
  'home',
  'outdoor',
  'aperitif',
  'together',
  'vaccinated',
  'not',
  'happening',
  'many',
  'italian',
  'cities'],
 ['miss', 'guys'],
 ['great', 'idea'],
 ['point',
 

In [27]:
tokenised_trigrams

[['kyrie', 'gets', 'vaccinated', 'trade', 'lol'],
 ['california',
  'health',
  'officials_announced',
  'monday',
  'state',
  'indoor',
  'mask',
  'mandate',
  'vaccinated',
  'people',
  'ending',
  'next_week',
  'expect'],
 ['yes',
  'quincy',
  'sam',
  'would',
  'figure',
  'certain',
  'good',
  'call',
  'say',
  'though',
  'want',
  'get',
  'kojak',
  'involved',
  'recently',
  'monk',
  'would',
  'sort',
  'well'],
 ['lol', 'not', 'getting', 'vaccinated'],
 ['ninety',
  'truckers',
  'double',
  'vaccinated',
  'sure',
  'keep',
  'believing',
  'working',
  'class',
  'movement'],
 ['not', 'talking', 'oxford', 'critical', 'theory', 'definition'],
 ['people',
  'milan',
  'refuse',
  'show',
  'health',
  'passport',
  'enter',
  'bars_restaurants',
  'decided',
  'bring',
  'food',
  'drink',
  'home',
  'outdoor',
  'aperitif',
  'together',
  'vaccinated',
  'not',
  'happening',
  'many',
  'italian',
  'cities'],
 ['miss', 'guys'],
 ['great', 'idea'],
 ['point',
 

## Lemmatization

### Lemmatization with all postags

In [28]:
nltk.download('wordnet')

[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\rachel\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [29]:
# TEST: lemmatisation of test_stopremoved
from nltk.stem import WordNetLemmatizer
lemmatizer=WordNetLemmatizer()
test_lemmatized = [lemmatizer.lemmatize(w)for w in test_stopremoved]
print(test_lemmatized)

['not', 'great', 'color', 'cruelty', 'free', 'use', 'elf', 'cosmetic', 'every', 'day', 'love']


In [30]:
#normal lemmatization of tokenised_stopremoved
from nltk.stem import WordNetLemmatizer
lemmatizer=WordNetLemmatizer()
tokenised_lemmatized_1 = [[lemmatizer.lemmatize(w) for w in each] for each in tokenised_bigrams]
tokenised_lemmatized_1

[['kyrie', 'get', 'vaccinated', 'trade', 'lol'],
 ['california',
  'health',
  'officials_announced',
  'monday',
  'state',
  'indoor',
  'mask',
  'mandate',
  'vaccinated',
  'people',
  'ending',
  'next_week',
  'expect'],
 ['yes',
  'quincy',
  'sam',
  'would',
  'figure',
  'certain',
  'good',
  'call',
  'say',
  'though',
  'want',
  'get',
  'kojak',
  'involved',
  'recently',
  'monk',
  'would',
  'sort',
  'well'],
 ['lol', 'not', 'getting', 'vaccinated'],
 ['ninety',
  'trucker',
  'double',
  'vaccinated',
  'sure',
  'keep',
  'believing',
  'working',
  'class',
  'movement'],
 ['not', 'talking', 'oxford', 'critical', 'theory', 'definition'],
 ['people',
  'milan',
  'refuse',
  'show',
  'health',
  'passport',
  'enter',
  'bars_restaurants',
  'decided',
  'bring',
  'food',
  'drink',
  'home',
  'outdoor',
  'aperitif',
  'together',
  'vaccinated',
  'not',
  'happening',
  'many',
  'italian',
  'city'],
 ['miss', 'guy'],
 ['great', 'idea'],
 ['point',
  'get

### Lemmatisation with noun, adj, verb and adv

In [31]:
def lemmatization(texts, allowed_postags=['NOUN', 'ADJ', 'VERB', 'ADV']):
    """https://spacy.io/api/annotation"""
    texts_out = []
    for sent in texts:
        doc = nlp(" ".join(sent)) 
        texts_out.append([token.lemma_ for token in doc if token.pos_ in allowed_postags])
    return texts_out

In [32]:
import spacy 

# Initialize spacy 'en' model, keeping only tagger component (for efficiency)
nlp = spacy.load("en_core_web_sm", disable=['parser', 'ner'])

# Do lemmatization keeping only noun, adj, vb, adv
tokenised_lemmatized_2 = lemmatization(tokenised_bigrams, allowed_postags=['NOUN', 'ADJ', 'VERB', 'ADV'])
tokenised_lemmatized_2

OSError: [E050] Can't find model 'en_core_web_sm'. It doesn't seem to be a Python package or a valid path to a data directory.

### Lemmatisation with nouns only

In [ ]:
def lemmatization_noun(texts, allowed_postags=['NOUN']):
    """https://spacy.io/api/annotation"""
    texts_out = []
    for sent in texts:
        doc = nlp(" ".join(sent)) 
        texts_out.append([token.lemma_ for token in doc if token.pos_ in allowed_postags])
    return texts_out

In [ ]:
import spacy 

# Initialize spacy 'en' model, keeping only tagger component (for efficiency)
nlp = spacy.load("en_core_web_sm", disable=['parser', 'ner'])

# Do lemmatization keeping only noun, adj, vb, adv
tokenised_lemmatized_3 = lemmatization_noun(tokenised_bigrams, allowed_postags=['NOUN'])
tokenised_lemmatized_3

### Gibberish Remover

In [ ]:
#test
trial_nested=[['happy', 'time', 'ajsdnkfjak'],[],[],['dsnfkajka','yo','wassup']]

In [ ]:
#test
len([])

if len([])== False:
    print('hi')

In [ ]:
#test
from gibberish_detector import detector
# load the gibberish detection model
Detector = detector.create_from_model('../Gibberish-Detector-master/gibberish-detector.model')

##change variable tokenised_lemmatized_x

new_list = []

for alist in trial_nested:
    mini_list = []
    if len(alist):
        for word in alist:
            test = Detector.is_gibberish(word)
            if test == False:
                mini_list.append(word)
    new_list.append(mini_list)

In [ ]:
#test
new_list

In [ ]:
#this is for tokenised_lemmatized_1
from gibberish_detector import detector
# load the gibberish detection model
Detector = detector.create_from_model('../Gibberish-Detector-master/gibberish-detector.model')

##change variable tokenised_lemmatized_x
new_list = []

for alist in tokenised_lemmatized_1:
    mini_list = []
    if len(alist):
        for word in alist:
            test = Detector.is_gibberish(word)
            if test == False:
                mini_list.append(word)
    new_list.append(mini_list)
    
tokenised_lemmatized_1 = new_list

In [ ]:
tokenised_lemmatized_1

In [ ]:
#this is for tokenised_lemmatized_2
from gibberish_detector import detector
# load the gibberish detection model
Detector = detector.create_from_model('../Gibberish-Detector-master/gibberish-detector.model')

##change variable tokenised_lemmatized_x
new_list2 = []

for alist in tokenised_lemmatized_2:
    mini_list = []
    if len(alist):
        for word in alist:
            test = Detector.is_gibberish(word)
            if test == False:
                mini_list.append(word)
    new_list2.append(mini_list)
                
tokenised_lemmatized_2 = new_list2

In [ ]:
tokenised_lemmatized_2

In [ ]:
#this is for tokenised_lemmatized_3
from gibberish_detector import detector
# load the gibberish detection model
Detector = detector.create_from_model('../Gibberish-Detector-master/gibberish-detector.model')

##change variable tokenised_lemmatized_x
new_list3 = []

for alist in tokenised_lemmatized_3:
    mini_list = []
    if len(alist):
        for word in alist:
            test = Detector.is_gibberish(word)
            if test == False:
                mini_list.append(word)
    new_list3.append(mini_list)
                
tokenised_lemmatized_3 = new_list3

In [ ]:
tokenised_lemmatized_3

## Creating column with Pre-processed words

In [ ]:
df["words_processed_all"] = tokenised_lemmatized_1
df["words_processed_noun_adj_verb_adv"] = tokenised_lemmatized_2
df["words_processed_noun"] = tokenised_lemmatized_3

In [ ]:
df.head()

In [ ]:
df.to_csv('usa-v2-preprocessed.csv')

## TFIDF

In [ ]:
df['words_processed_all']

In [ ]:
def listToString(s): 
    # initialize an empty string
    str1 = "" 
    # traverse in the string  
    for ele in s: 
        str1 += ele  
    # return string  
    return str1

In [ ]:
newlist = []

for each in df['words_processed_all']:
    new = each.strip("][").replace("'","").split(", ")
    newlist.append(new)

In [ ]:
newlist

In [ ]:
joined_list = []

for lis in newlist:
    new = " ".join(lis)
    joined_list.append(new)

In [ ]:
joined_list

In [ ]:
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.feature_extraction.text import CountVectorizer

In [ ]:
import pandas as pd
cv = CountVectorizer()
word_count_vector = cv.fit_transform(joined_list)
tf = pd.DataFrame(word_count_vector.toarray(), columns=cv.get_feature_names())
print(tf)

In [ ]:
tfidf_transformer = TfidfTransformer()
X = tfidf_transformer.fit_transform(word_count_vector)
idf = pd.DataFrame({'feature_name':cv.get_feature_names(), 'idf_weights':tfidf_transformer.idf_})
idf.sort_values('idf_weights', ascending=False, inplace=True)

In [ ]:
idf.to_csv('tfidf-descending.csv')

In [ ]:
tf_idf = pd.DataFrame(X.toarray(),columns=cv.get_feature_names())
tf_idf